In [0]:
import pandas as pd
from kafka import KafkaConsumer, KafkaProducer
from time import sleep
from json import dumps
import json

In [0]:
producer = KafkaProducer(
    bootstrap_servers = ['54.245.47.165:9092'], 
    value_serializer = lambda x:
    dumps(x).encode('utf-8')
    )

In [0]:
%sh
wget http://phoenixnap.dl.sourceforge.net/project/ta-lib/ta-lib/0.4.0/ta-lib-0.4.0-src.tar.gz \
  && sudo tar -xzf ta-lib-0.4.0-src.tar.gz \
  && sudo rm ta-lib-0.4.0-src.tar.gz \
  && cd ta-lib/ \
  && sudo ./configure --prefix=/usr \
  && sudo make \
  && sudo make install \
  && cd ~ \
  && sudo rm -rf ta-lib/ \
  && pip install ta-lib

--2023-05-05 22:16:55--  http://phoenixnap.dl.sourceforge.net/project/ta-lib/ta-lib/0.4.0/ta-lib-0.4.0-src.tar.gz
Resolving phoenixnap.dl.sourceforge.net (phoenixnap.dl.sourceforge.net)... 184.164.141.26
Connecting to phoenixnap.dl.sourceforge.net (phoenixnap.dl.sourceforge.net)|184.164.141.26|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1330299 (1.3M) [application/x-gzip]
Saving to: ‘ta-lib-0.4.0-src.tar.gz’

     0K .......... .......... .......... .......... ..........  3%  668K 2s
    50K .......... .......... .......... .......... ..........  7% 1.29M 1s
   100K .......... .......... .......... .......... .......... 11% 1.28M 1s
   150K .......... .......... .......... .......... .......... 15%  676K 1s
   200K .......... .......... .......... .......... .......... 19% 1.31M 1s
   250K .......... .......... .......... .......... .......... 23% 1.29M 1s
   300K .......... .......... .......... .......... .......... 26% 1.27M 1s
   350K .......... .......

In [0]:
import datetime
import yfinance as yf
import pandas as pd
from datetime import date
from datetime import timedelta
import talib as ta

end = datetime.datetime.now()
start_52 = end - datetime.timedelta(weeks=52)
start = end - timedelta(days=10)
print(start,end)

2023-04-25 22:20:25.846946 2023-05-05 22:20:25.846946


In [0]:
data_df = yf.download('AAPL', start, end, interval='5m')
print(data_df)

[*********************100%***********************]  1 of 1 completed
                                 Open        High         Low       Close  \
Datetime                                                                    
2023-04-26 09:30:00-04:00  163.054993  164.110001  162.800003  163.580002   
2023-04-26 09:35:00-04:00  163.600006  163.839996  163.427200  163.720001   
2023-04-26 09:40:00-04:00  163.729996  163.750000  163.250000  163.419998   
2023-04-26 09:45:00-04:00  163.419998  164.050003  163.330002  163.869995   
2023-04-26 09:50:00-04:00  163.850006  164.139999  163.690002  163.835007   
...                               ...         ...         ...         ...   
2023-05-05 15:35:00-04:00  173.759995  173.880005  173.690002  173.817902   
2023-05-05 15:40:00-04:00  173.809998  173.940002  173.779999  173.929993   
2023-05-05 15:45:00-04:00  173.929993  174.000000  173.475006  173.589996   
2023-05-05 15:50:00-04:00  173.580002  173.725006  173.350006  173.652206   
2023-05

In [0]:
# -------------------SMA--------------------------- 

data_df['sma_10'] = ta.SMA(data_df['Close'], timeperiod=10)


# -------------------EMA--------------------------- 

data_df['ema_20'] = ta.EMA(data_df['Close'], timeperiod=20)


#---------------------RSI----------------------------

data_df['rsi_14'] = ta.RSI(data_df['Close'], timeperiod=14)


#-------------------MACD------------------------------

data_df['macd'], data_df['macdsignal'], data_df['macdhist'] = ta.MACD(data_df['Close'], fastperiod=12, slowperiod=26, signalperiod=9)

In [0]:
df = spark.createDataFrame(data_df)
df.display()

Open High Low Close Adj Close Volume sma_10 ema_20 rsi_14 macd macdsignal macdhist 163.05499267578125 164.11000061035156 162.8000030517578 163.5800018310547 163.5800018310547 3661385 null null null null null null 163.60000610351562 163.83999633789062 163.4272003173828 163.72000122070312 163.72000122070312 858738 null null null null null null 163.72999572753906 163.75 163.25 163.4199981689453 163.4199981689453 684919 null null null null null null 163.4199981689453 164.0500030517578 163.3300018310547 163.8699951171875 163.8699951171875 989460 null null null null null null 163.85000610351562 164.13999938964844 163.69000244140625 163.8350067138672 163.8350067138672 783603 null null null null null null 163.82479858398438 164.10000610351562 163.7899932861328 164.0290985107422 164.0290985107422 571546 null null null null null null 164.02000427246094 164.0449981689453 163.55999755859375 163.67999267578125 163.67999267578125 550998 null null null null null null 163.69000244140625 163.9600067138672 163.69000244140625 163.91000366210938 163.91000366210938 484684 null null null null null null 163.91000366210938 164.26930236816406 163.87579345703125 164.00999450683594 164.00999450683594 600273 null null null null null null 164.02000427246094 164.02000427246094 163.6300048828125 163.7239990234375 163.7239990234375 614822 163.7778091430664 null null null null null 163.720703125 163.77000427246094 163.4499969482422 163.60000610351562 163.60000610351562 567483 163.7798095703125 null null null null null 163.57000732421875 163.60000610351562 163.26499938964844 163.3105926513672 163.3105926513672 561460 163.7388687133789 null null null null null 163.30999755859375 163.8350067138672 163.27000427246094 163.69000244140625 163.69000244140625 553156 163.765869140625 null null null null null 163.67999267578125 163.72000122070312 163.44500732421875 163.5749969482422 163.5749969482422 351731 163.73636932373046 null null null null null 163.5709991455078 163.77000427246094 163.47999572753906 163.65989685058594 163.65989685058594 393069 163.71885833740234 null 51.2983019915893 null null null 163.65499877929688 164.07000732421875 163.63999938964844 164.0449981689453 164.0449981689453 408099 163.72044830322267 null 57.08293386079396 null null null 164.04820251464844 164.1699981689453 163.92999267578125 163.9700927734375 163.9700927734375 392094 163.74945831298828 null 55.697175293369384 null null null 163.97000122070312 164.25999450683594 163.88999938964844 164.18499755859375 164.18499755859375 434469 163.7769577026367 null 58.788319579010064 null null null 164.19000244140625 164.5500030517578 164.08999633789062 164.5500030517578 164.5500030517578 633865 163.8309585571289 null 63.45257801393656 null null null 164.5500030517578 164.639892578125 164.38999938964844 164.57000732421875 164.57000732421875 487542 163.91555938720703 163.84668426513673 63.69509137696774 null null null 164.5800018310547 164.7100067138672 164.52000427246094 164.66209411621094 164.66209411621094 381013 164.02176818847656 163.92434234619142 64.85132901124088 null null null 164.6699981689453 164.75999450683594 164.57000732421875 164.72000122070312 164.72000122070312 354861 164.16270904541017 164.0001193818592 65.59339539628478 null null null 164.74000549316406 164.88499450683594 164.67999267578125 164.78970336914062 164.78970336914062 516770 164.2726791381836 164.07531785683838 66.50993007738819 null null null 164.7899932861328 164.7899932861328 164.5399932861328 164.6199951171875 164.6199951171875 439852 164.37717895507814 164.12719188163354 62.167695007267774 null null null 164.6199951171875 164.72000122070312 164.50999450683594 164.5500030517578 164.5500030517578 314294 164.4661895751953 164.16745961212158 60.415800675123364 null null null 164.5500030517578 164.6199951171875 164.39999389648438 164.61000061035156 164.61000061035156 380711 164.52268981933594 164.20960637385775 61.41944777565509 null null null 164.6300048828125 164.83999633789062 164.57000732421875 164.8125 164.8125 345370

In [0]:
from pyspark.sql.functions import *
df = df.withColumn("Ticker", lit('AAPL'))

In [0]:
# Strategy 1 - Using SMA and EMA
from pyspark.sql.functions import *
df1 = df.withColumn("Signal",
      when(((df['sma_10']) > (df['ema_20'])), lit("Buy")) 
     .when(((df['sma_10']) < (df['ema_20'])), lit("Sell"))
     .otherwise(lit("hold")))

In [0]:
display(df1)

Open High Low Close Adj Close Volume sma_10 ema_20 rsi_14 macd macdsignal macdhist Ticker Signal 163.05499267578125 164.11000061035156 162.8000030517578 163.5800018310547 163.5800018310547 3661385 null null null null null null AAPL hold 163.60000610351562 163.83999633789062 163.4272003173828 163.72000122070312 163.72000122070312 858738 null null null null null null AAPL hold 163.72999572753906 163.75 163.25 163.4199981689453 163.4199981689453 684919 null null null null null null AAPL hold 163.4199981689453 164.0500030517578 163.3300018310547 163.8699951171875 163.8699951171875 989460 null null null null null null AAPL hold 163.85000610351562 164.13999938964844 163.69000244140625 163.8350067138672 163.8350067138672 783603 null null null null null null AAPL hold 163.82479858398438 164.10000610351562 163.7899932861328 164.0290985107422 164.0290985107422 571546 null null null null null null AAPL hold 164.02000427246094 164.0449981689453 163.55999755859375 163.67999267578125 163.67999267578125 550998 null null null null null null AAPL hold 163.69000244140625 163.9600067138672 163.69000244140625 163.91000366210938 163.91000366210938 484684 null null null null null null AAPL hold 163.91000366210938 164.26930236816406 163.87579345703125 164.00999450683594 164.00999450683594 600273 null null null null null null AAPL hold 164.02000427246094 164.02000427246094 163.6300048828125 163.7239990234375 163.7239990234375 614822 163.7778091430664 null null null null null AAPL hold 163.720703125 163.77000427246094 163.4499969482422 163.60000610351562 163.60000610351562 567483 163.7798095703125 null null null null null AAPL hold 163.57000732421875 163.60000610351562 163.26499938964844 163.3105926513672 163.3105926513672 561460 163.7388687133789 null null null null null AAPL hold 163.30999755859375 163.8350067138672 163.27000427246094 163.69000244140625 163.69000244140625 553156 163.765869140625 null null null null null AAPL hold 163.67999267578125 163.72000122070312 163.44500732421875 163.5749969482422 163.5749969482422 351731 163.73636932373046 null null null null null AAPL hold 163.5709991455078 163.77000427246094 163.47999572753906 163.65989685058594 163.65989685058594 393069 163.71885833740234 null 51.2983019915893 null null null AAPL hold 163.65499877929688 164.07000732421875 163.63999938964844 164.0449981689453 164.0449981689453 408099 163.72044830322267 null 57.08293386079396 null null null AAPL hold 164.04820251464844 164.1699981689453 163.92999267578125 163.9700927734375 163.9700927734375 392094 163.74945831298828 null 55.697175293369384 null null null AAPL hold 163.97000122070312 164.25999450683594 163.88999938964844 164.18499755859375 164.18499755859375 434469 163.7769577026367 null 58.788319579010064 null null null AAPL hold 164.19000244140625 164.5500030517578 164.08999633789062 164.5500030517578 164.5500030517578 633865 163.8309585571289 null 63.45257801393656 null null null AAPL hold 164.5500030517578 164.639892578125 164.38999938964844 164.57000732421875 164.57000732421875 487542 163.91555938720703 163.84668426513673 63.69509137696774 null null null AAPL Buy 164.5800018310547 164.7100067138672 164.52000427246094 164.66209411621094 164.66209411621094 381013 164.02176818847656 163.92434234619142 64.85132901124088 null null null AAPL Buy 164.6699981689453 164.75999450683594 164.57000732421875 164.72000122070312 164.72000122070312 354861 164.16270904541017 164.0001193818592 65.59339539628478 null null null AAPL Buy 164.74000549316406 164.88499450683594 164.67999267578125 164.78970336914062 164.78970336914062 516770 164.2726791381836 164.07531785683838 66.50993007738819 null null null AAPL Buy 164.7899932861328 164.7899932861328 164.5399932861328 164.6199951171875 164.6199951171875 439852 164.37717895507814 164.12719188163354 62.167695007267774 null null null AAPL Buy 164.6199951171875 164.72000122070312 164.50999450683594 164.5500030517578 164.5500030517578 314294 164.4661895751953 164.16745961212158 60.415800675123364 null null null AA

In [0]:
# Strategy 2 - Considering Overbought and Oversold zones based on RSI
from pyspark.sql.functions import *
df2 = df.withColumn("Signal",
      when((df['rsi_14'] > 70) , lit("Overbought (Sell)")) 
     .when((df['rsi_14'] < 30) , lit("Oversold (Buy)"))
     .otherwise(lit("Neutral (hold)")))

In [0]:
display(df2)

Open High Low Close Adj Close Volume sma_10 ema_20 rsi_14 macd macdsignal macdhist Ticker Signal 163.05499267578125 164.11000061035156 162.8000030517578 163.5800018310547 163.5800018310547 3661385 null null null null null null AAPL Neutral (hold) 163.60000610351562 163.83999633789062 163.4272003173828 163.72000122070312 163.72000122070312 858738 null null null null null null AAPL Neutral (hold) 163.72999572753906 163.75 163.25 163.4199981689453 163.4199981689453 684919 null null null null null null AAPL Neutral (hold) 163.4199981689453 164.0500030517578 163.3300018310547 163.8699951171875 163.8699951171875 989460 null null null null null null AAPL Neutral (hold) 163.85000610351562 164.13999938964844 163.69000244140625 163.8350067138672 163.8350067138672 783603 null null null null null null AAPL Neutral (hold) 163.82479858398438 164.10000610351562 163.7899932861328 164.0290985107422 164.0290985107422 571546 null null null null null null AAPL Neutral (hold) 164.02000427246094 164.0449981689453 163.55999755859375 163.67999267578125 163.67999267578125 550998 null null null null null null AAPL Neutral (hold) 163.69000244140625 163.9600067138672 163.69000244140625 163.91000366210938 163.91000366210938 484684 null null null null null null AAPL Neutral (hold) 163.91000366210938 164.26930236816406 163.87579345703125 164.00999450683594 164.00999450683594 600273 null null null null null null AAPL Neutral (hold) 164.02000427246094 164.02000427246094 163.6300048828125 163.7239990234375 163.7239990234375 614822 163.7778091430664 null null null null null AAPL Neutral (hold) 163.720703125 163.77000427246094 163.4499969482422 163.60000610351562 163.60000610351562 567483 163.7798095703125 null null null null null AAPL Neutral (hold) 163.57000732421875 163.60000610351562 163.26499938964844 163.3105926513672 163.3105926513672 561460 163.7388687133789 null null null null null AAPL Neutral (hold) 163.30999755859375 163.8350067138672 163.27000427246094 163.69000244140625 163.69000244140625 553156 163.765869140625 null null null null null AAPL Neutral (hold) 163.67999267578125 163.72000122070312 163.44500732421875 163.5749969482422 163.5749969482422 351731 163.73636932373046 null null null null null AAPL Neutral (hold) 163.5709991455078 163.77000427246094 163.47999572753906 163.65989685058594 163.65989685058594 393069 163.71885833740234 null 51.2983019915893 null null null AAPL Neutral (hold) 163.65499877929688 164.07000732421875 163.63999938964844 164.0449981689453 164.0449981689453 408099 163.72044830322267 null 57.08293386079396 null null null AAPL Neutral (hold) 164.04820251464844 164.1699981689453 163.92999267578125 163.9700927734375 163.9700927734375 392094 163.74945831298828 null 55.697175293369384 null null null AAPL Neutral (hold) 163.97000122070312 164.25999450683594 163.88999938964844 164.18499755859375 164.18499755859375 434469 163.7769577026367 null 58.788319579010064 null null null AAPL Neutral (hold) 164.19000244140625 164.5500030517578 164.08999633789062 164.5500030517578 164.5500030517578 633865 163.8309585571289 null 63.45257801393656 null null null AAPL Neutral (hold) 164.5500030517578 164.639892578125 164.38999938964844 164.57000732421875 164.57000732421875 487542 163.91555938720703 163.84668426513673 63.69509137696774 null null null AAPL Neutral (hold) 164.5800018310547 164.7100067138672 164.52000427246094 164.66209411621094 164.66209411621094 381013 164.02176818847656 163.92434234619142 64.85132901124088 null null null AAPL Neutral (hold) 164.6699981689453 164.75999450683594 164.57000732421875 164.72000122070312 164.72000122070312 354861 164.16270904541017 164.0001193818592 65.59339539628478 null null null AAPL Neutral (hold) 164.74000549316406 164.88499450683594 164.67999267578125 164.78970336914062 164.78970336914062 516770 164.2726791381836 164.07531785683838 66.50993007738819 null null null AAPL Neutral (hold) 164.7899932861328 164.7899932861328 164.5399932861328 164.6199951171875 164.6199951171875 439852 164.37717895507814 

In [0]:
# Strategy 3 - Using macd, macdsignal and macdhist
from pyspark.sql.functions import *
df3 = df.withColumn("Buy_Signal", when((col("macd") > col("macdsignal")) & (col("macdhist") <= col("macdsignal")), "Buy").otherwise("Hold")) \
                 .withColumn("Sell_Signal", when((col("macd") < col("macdsignal")) & (col("macdhist") >= col("macdsignal")), "Sell").otherwise("Hold")) 

In [0]:
display(df3)

Open High Low Close Adj Close Volume sma_10 ema_20 rsi_14 macd macdsignal macdhist Ticker Buy_Signal Sell_Signal 163.05499267578125 164.11000061035156 162.8000030517578 163.5800018310547 163.5800018310547 3661385 null null null null null null AAPL Hold Hold 163.60000610351562 163.83999633789062 163.4272003173828 163.72000122070312 163.72000122070312 858738 null null null null null null AAPL Hold Hold 163.72999572753906 163.75 163.25 163.4199981689453 163.4199981689453 684919 null null null null null null AAPL Hold Hold 163.4199981689453 164.0500030517578 163.3300018310547 163.8699951171875 163.8699951171875 989460 null null null null null null AAPL Hold Hold 163.85000610351562 164.13999938964844 163.69000244140625 163.8350067138672 163.8350067138672 783603 null null null null null null AAPL Hold Hold 163.82479858398438 164.10000610351562 163.7899932861328 164.0290985107422 164.0290985107422 571546 null null null null null null AAPL Hold Hold 164.02000427246094 164.0449981689453 163.55999755859375 163.67999267578125 163.67999267578125 550998 null null null null null null AAPL Hold Hold 163.69000244140625 163.9600067138672 163.69000244140625 163.91000366210938 163.91000366210938 484684 null null null null null null AAPL Hold Hold 163.91000366210938 164.26930236816406 163.87579345703125 164.00999450683594 164.00999450683594 600273 null null null null null null AAPL Hold Hold 164.02000427246094 164.02000427246094 163.6300048828125 163.7239990234375 163.7239990234375 614822 163.7778091430664 null null null null null AAPL Hold Hold 163.720703125 163.77000427246094 163.4499969482422 163.60000610351562 163.60000610351562 567483 163.7798095703125 null null null null null AAPL Hold Hold 163.57000732421875 163.60000610351562 163.26499938964844 163.3105926513672 163.3105926513672 561460 163.7388687133789 null null null null null AAPL Hold Hold 163.30999755859375 163.8350067138672 163.27000427246094 163.69000244140625 163.69000244140625 553156 163.765869140625 null null null null null AAPL Hold Hold 163.67999267578125 163.72000122070312 163.44500732421875 163.5749969482422 163.5749969482422 351731 163.73636932373046 null null null null null AAPL Hold Hold 163.5709991455078 163.77000427246094 163.47999572753906 163.65989685058594 163.65989685058594 393069 163.71885833740234 null 51.2983019915893 null null null AAPL Hold Hold 163.65499877929688 164.07000732421875 163.63999938964844 164.0449981689453 164.0449981689453 408099 163.72044830322267 null 57.08293386079396 null null null AAPL Hold Hold 164.04820251464844 164.1699981689453 163.92999267578125 163.9700927734375 163.9700927734375 392094 163.74945831298828 null 55.697175293369384 null null null AAPL Hold Hold 163.97000122070312 164.25999450683594 163.88999938964844 164.18499755859375 164.18499755859375 434469 163.7769577026367 null 58.788319579010064 null null null AAPL Hold Hold 164.19000244140625 164.5500030517578 164.08999633789062 164.5500030517578 164.5500030517578 633865 163.8309585571289 null 63.45257801393656 null null null AAPL Hold Hold 164.5500030517578 164.639892578125 164.38999938964844 164.57000732421875 164.57000732421875 487542 163.91555938720703 163.84668426513673 63.69509137696774 null null null AAPL Hold Hold 164.5800018310547 164.7100067138672 164.52000427246094 164.66209411621094 164.66209411621094 381013 164.02176818847656 163.92434234619142 64.85132901124088 null null null AAPL Hold Hold 164.6699981689453 164.75999450683594 164.57000732421875 164.72000122070312 164.72000122070312 354861 164.16270904541017 164.0001193818592 65.59339539628478 null null null AAPL Hold Hold 164.74000549316406 164.88499450683594 164.67999267578125 164.78970336914062 164.78970336914062 516770 164.2726791381836 164.07531785683838 66.50993007738819 null null null AAPL Hold Hold 164.7899932861328 164.7899932861328 164.5399932861328 164.6199951171875 164.6199951171875 439852 164.37717895507814 164.12719188163354 62.167695007267774 null null null AAPL Hold Hold 164.6199951171875 164.720001220

In [0]:
# Sending the data on kafka
for row in df1.collect():
    dict_stock = row.asDict()
    producer.send('demo_testing1', value=dict_stock)
    sleep(5)

In [0]:
# Sending the data on kafka
for row in df2.collect():
    dict_stock = row.asDict()
    producer.send('demo_testing1', value=dict_stock)
    sleep(5)

In [0]:
# Sending the data on kafka
for row in df3.collect():
    dict_stock = row.asDict()
    producer.send('demo_testing2', value=dict_stock)
    sleep(5)

In [0]:
df_aarti = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/shailpatel2811@gmail.com/APOLLOHOSP__EQ__NSE__NSE__MINUTE.csv")
df_aarti = df_aarti.withColumn('Ticker', lit('APOLLOHOS'))
display(df_aarti)

timestamp open high low close volume Ticker 2017-01-02 09:15:00+05:30 1180.0 1180.0 1171.0 1174.9 458.0 APOLLOHOS 2017-01-02 09:16:00+05:30 1172.2 1181.7 1172.2 1178.6 326.0 APOLLOHOS 2017-01-02 09:17:00+05:30 1179.55 1182.45 1177.9 1177.9 486.0 APOLLOHOS 2017-01-02 09:18:00+05:30 1177.9 1178.7 1177.9 1178.25 443.0 APOLLOHOS 2017-01-02 09:19:00+05:30 1178.25 1178.25 1178.25 1178.25 130.0 APOLLOHOS 2017-01-02 09:20:00+05:30 1178.25 1178.25 1174.85 1174.85 262.0 APOLLOHOS 2017-01-02 09:21:00+05:30 1174.85 1175.0 1172.1 1173.9 228.0 APOLLOHOS 2017-01-02 09:22:00+05:30 1173.9 1174.0 1172.0 1173.25 281.0 APOLLOHOS 2017-01-02 09:23:00+05:30 1173.25 1173.65 1173.25 1173.45 35.0 APOLLOHOS 2017-01-02 09:24:00+05:30 1174.0 1174.7 1174.0 1174.7 298.0 APOLLOHOS 2017-01-02 09:25:00+05:30 1174.7 1179.5 1174.7 1179.5 174.0 APOLLOHOS 2017-01-02 09:26:00+05:30 1178.1 1178.55 1178.05 1178.55 32.0 APOLLOHOS 2017-01-02 09:27:00+05:30 1180.0 1182.35 1180.0 1181.9 951.0 APOLLOHOS 2017-01-02 09:28:00+05:30 1180.65 1181.95 1180.65 1181.4 128.0 APOLLOHOS 2017-01-02 09:29:00+05:30 1181.4 1181.4 1180.5 1180.5 20.0 APOLLOHOS 2017-01-02 09:30:00+05:30 1180.5 1180.5 1177.0 1177.0 240.0 APOLLOHOS 2017-01-02 09:31:00+05:30 1177.0 1177.1 1177.0 1177.1 20.0 APOLLOHOS 2017-01-02 09:32:00+05:30 1177.1 1178.4 1176.3 1176.3 54.0 APOLLOHOS 2017-01-02 09:33:00+05:30 1176.3 1180.2 1176.3 1180.2 192.0 APOLLOHOS 2017-01-02 09:34:00+05:30 1180.2 1180.2 1179.3 1179.3 73.0 APOLLOHOS 2017-01-02 09:35:00+05:30 1179.3 1179.3 1179.2 1179.2 5.0 APOLLOHOS 2017-01-02 09:36:00+05:30 1179.2 1180.1 1179.2 1180.1 232.0 APOLLOHOS 2017-01-02 09:37:00+05:30 1180.1 1181.75 1180.0 1181.75 142.0 APOLLOHOS 2017-01-02 09:38:00+05:30 1181.75 1181.75 1180.25 1180.25 20.0 APOLLOHOS 2017-01-02 09:39:00+05:30 1180.25 1182.0 1180.25 1182.0 149.0 APOLLOHOS 2017-01-02 09:40:00+05:30 1182.0 1183.0 1182.0 1183.0 507.0 APOLLOHOS 2017-01-02 09:41:00+05:30 1183.0 1183.0 1182.9 1182.9 1.0 APOLLOHOS 2017-01-02 09:42:00+05:30 1182.55 1182.55 1181.5 1181.5 151.0 APOLLOHOS 2017-01-02 09:43:00+05:30 1181.5 1182.45 1181.0 1182.45 89.0 APOLLOHOS 2017-01-02 09:44:00+05:30 1182.45 1182.95 1182.0 1182.3 225.0 APOLLOHOS 2017-01-02 09:45:00+05:30 1182.3 1182.3 1182.3 1182.3 0.0 APOLLOHOS 2017-01-02 09:46:00+05:30 1182.3 1182.3 1182.3 1182.3 0.0 APOLLOHOS 2017-01-02 09:47:00+05:30 1182.3 1182.3 1181.4 1181.4 34.0 APOLLOHOS 2017-01-02 09:48:00+05:30 1181.4 1181.6 1181.4 1181.6 25.0 APOLLOHOS 2017-01-02 09:49:00+05:30 1181.6 1181.6 1181.6 1181.6 72.0 APOLLOHOS 2017-01-02 09:50:00+05:30 1181.6 1181.6 1180.55 1180.55 50.0 APOLLOHOS 2017-01-02 09:51:00+05:30 1180.55 1181.0 1180.0 1181.0 457.0 APOLLOHOS 2017-01-02 09:52:00+05:30 1181.0 1181.0 1180.5 1181.0 83.0 APOLLOHOS 2017-01-02 09:53:00+05:30 1181.0 1182.0 1181.0 1181.25 100.0 APOLLOHOS 2017-01-02 09:54:00+05:30 1181.25 1181.25 1181.25 1181.25 250.0 APOLLOHOS 2017-01-02 09:55:00+05:30 1181.25 1182.4 1181.25 1182.4 58.0 APOLLOHOS 2017-01-02 09:56:00+05:30 1182.4 1183.0 1182.4 1183.0 354.0 APOLLOHOS 2017-01-02 09:57:00+05:30 1183.0 1183.0 1182.5 1182.5 3.0 APOLLOHOS 2017-01-02 09:58:00+05:30 1182.5 1183.3 1182.5 1183.3 266.0 APOLLOHOS 2017-01-02 09:59:00+05:30 1183.3 1183.3 1183.15 1183.15 10.0 APOLLOHOS 2017-01-02 10:00:00+05:30 1183.15 1183.3 1183.15 1183.3 77.0 APOLLOHOS 2017-01-02 10:01:00+05:30 1183.3 1183.3 1183.3 1183.3 0.0 APOLLOHOS 2017-01-02 10:02:00+05:30 1183.3 1183.3 1183.3 1183.3 0.0 APOLLOHOS 2017-01-02 10:03:00+05:30 1183.3 1183.3 1183.25 1183.25 144.0 APOLLOHOS 2017-01-02 10:04:00+05:30 1183.25 1185.0 1183.25 1184.8 232.0 APOLLOHOS 2017-01-02 10:05:00+05:30 1185.85 1188.5 1184.8 1187.65 978.0 APOLLOHOS 2017-01-02 10:06:00+05:30 1187.65 1187.65 1186.05 1186.05 116.0 APOLLOHOS 2017-01-02 10:07:00+05:30 1186.05 1187.55 1186.0 1186.0 147.0 APOLLOHOS 2017-01-02 10:08:00+05:30 1186.0 1186.6 1184.8 1186.6 208.0 APOLLOHOS 2017-01-02 10:09:00+05:30 1186.6 1186.9 1186.6 1186.9 190.0 APOLLOHOS 2017-01-02 10:10:00+05:30 1186.9 1188.25 1186.25 1187.0 296.0 APOLLOHOS 

In [0]:
df_aarti = (df_aarti.withColumnRenamed('open', 'Open')
            .withColumnRenamed('high', 'High')
            .withColumnRenamed('low', 'Low')
            .withColumnRenamed('close', 'Close'))

In [0]:
data_df_aarti = df_aarti.toPandas()

In [0]:
# -------------------SMA--------------------------- 

data_df_aarti['sma_10'] = ta.SMA(data_df_aarti['Close'], timeperiod=10)


# -------------------EMA--------------------------- 

data_df_aarti['ema_20'] = ta.EMA(data_df_aarti['Close'], timeperiod=20)


#---------------------RSI----------------------------

data_df_aarti['rsi_14'] = ta.RSI(data_df_aarti['Close'], timeperiod=14)


#-------------------MACD------------------------------

data_df_aarti['macd'], data_df_aarti['macdsignal'], data_df_aarti['macdhist'] = ta.MACD(data_df_aarti['Close'], fastperiod=12, slowperiod=26, signalperiod=9)

In [0]:
df_aarti = spark.createDataFrame(data_df_aarti)
df_aarti.display()

timestamp Open High Low Close volume Ticker sma_10 ema_20 rsi_14 macd macdsignal macdhist 2017-01-02 09:15:00+05:30 1180.0 1180.0 1171.0 1174.9 458.0 APOLLOHOS null null null null null null 2017-01-02 09:16:00+05:30 1172.2 1181.7 1172.2 1178.6 326.0 APOLLOHOS null null null null null null 2017-01-02 09:17:00+05:30 1179.55 1182.45 1177.9 1177.9 486.0 APOLLOHOS null null null null null null 2017-01-02 09:18:00+05:30 1177.9 1178.7 1177.9 1178.25 443.0 APOLLOHOS null null null null null null 2017-01-02 09:19:00+05:30 1178.25 1178.25 1178.25 1178.25 130.0 APOLLOHOS null null null null null null 2017-01-02 09:20:00+05:30 1178.25 1178.25 1174.85 1174.85 262.0 APOLLOHOS null null null null null null 2017-01-02 09:21:00+05:30 1174.85 1175.0 1172.1 1173.9 228.0 APOLLOHOS null null null null null null 2017-01-02 09:22:00+05:30 1173.9 1174.0 1172.0 1173.25 281.0 APOLLOHOS null null null null null null 2017-01-02 09:23:00+05:30 1173.25 1173.65 1173.25 1173.45 35.0 APOLLOHOS null null null null null null 2017-01-02 09:24:00+05:30 1174.0 1174.7 1174.0 1174.7 298.0 APOLLOHOS 1175.805 null null null null null 2017-01-02 09:25:00+05:30 1174.7 1179.5 1174.7 1179.5 174.0 APOLLOHOS 1176.265 null null null null null 2017-01-02 09:26:00+05:30 1178.1 1178.55 1178.05 1178.55 32.0 APOLLOHOS 1176.26 null null null null null 2017-01-02 09:27:00+05:30 1180.0 1182.35 1180.0 1181.9 951.0 APOLLOHOS 1176.66 null null null null null 2017-01-02 09:28:00+05:30 1180.65 1181.95 1180.65 1181.4 128.0 APOLLOHOS 1176.975 null null null null null 2017-01-02 09:29:00+05:30 1181.4 1181.4 1180.5 1180.5 20.0 APOLLOHOS 1177.2 null 62.903225806451516 null null null 2017-01-02 09:30:00+05:30 1180.5 1180.5 1177.0 1177.0 240.0 APOLLOHOS 1177.415 null 53.594080338266224 null null null 2017-01-02 09:31:00+05:30 1177.0 1177.1 1177.0 1177.1 20.0 APOLLOHOS 1177.7350000000001 null 53.80443581026353 null null null 2017-01-02 09:32:00+05:30 1177.1 1178.4 1176.3 1176.3 54.0 APOLLOHOS 1178.04 null 51.78218296439206 null null null 2017-01-02 09:33:00+05:30 1176.3 1180.2 1176.3 1180.2 192.0 APOLLOHOS 1178.715 null 59.728631345031616 null null null 2017-01-02 09:34:00+05:30 1180.2 1180.2 1179.3 1179.3 73.0 APOLLOHOS 1179.1749999999997 1177.49 57.37857712627243 null null null 2017-01-02 09:35:00+05:30 1179.3 1179.3 1179.2 1179.2 5.0 APOLLOHOS 1179.145 1177.652857142857 57.109703996805685 null null null 2017-01-02 09:36:00+05:30 1179.2 1180.1 1179.2 1180.1 232.0 APOLLOHOS 1179.3 1177.885918367347 58.9730522424587 null null null 2017-01-02 09:37:00+05:30 1180.1 1181.75 1180.0 1181.75 142.0 APOLLOHOS 1179.285 1178.2539261418854 62.21413741716577 null null null 2017-01-02 09:38:00+05:30 1181.75 1181.75 1180.25 1180.25 20.0 APOLLOHOS 1179.17 1178.4440284140867 57.74782722141104 null null null 2017-01-02 09:39:00+05:30 1180.25 1182.0 1180.25 1182.0 149.0 APOLLOHOS 1179.3200000000002 1178.78269237465 61.24353727736097 null null null 2017-01-02 09:40:00+05:30 1182.0 1183.0 1182.0 1183.0 507.0 APOLLOHOS 1179.92 1179.1843407199215 63.12116786279181 null null null 2017-01-02 09:41:00+05:30 1183.0 1183.0 1182.9 1182.9 1.0 APOLLOHOS 1180.5 1179.5382130323098 62.79355137672242 null null null 2017-01-02 09:42:00+05:30 1182.55 1182.55 1181.5 1181.5 151.0 APOLLOHOS 1181.02 1179.7250498863755 58.236356141346114 null null null 2017-01-02 09:43:00+05:30 1181.5 1182.45 1181.0 1182.45 89.0 APOLLOHOS 1181.2450000000001 1179.984568944816 60.339739364817824 null null null 2017-01-02 09:44:00+05:30 1182.45 1182.95 1182.0 1182.3 225.0 APOLLOHOS 1181.545 1180.205086188167 59.827382731383324 null null null 2017-01-02 09:45:00+05:30 1182.3 1182.3 1182.3 1182.3 0.0 APOLLOHOS 1181.855 1180.4046017892938 59.827382731383324 null null null 2017-01-02 09:46:00+05:30 1182.3 1182.3 1182.3 1182.3 0.0 APOLLOHOS 1182.0749999999998 1180.5851159045992 59.82738273138332 null null null 2017-01-02 09:47:00+05:30 1182.3 1182.3 1181.4 1181.4 34.0 APOLLOHOS 1182.0399999999997 1180.662723913685 56.24820781294806 null null null 2017-01-02 09

In [0]:
# Strategy 1 - Using SMA and EMA
from pyspark.sql.functions import *
df1_aarti = df_aarti.withColumn("Signal",
      when(((df_aarti['sma_10']) > (df_aarti['ema_20'])), lit("Buy")) 
     .when(((df_aarti['sma_10']) < (df_aarti['ema_20'])), lit("Sell"))
     .otherwise(lit("hold")))

In [0]:
# Strategy 2 - Considering Overbought and Oversold zones based on RSI
from pyspark.sql.functions import *
df2_aarti = df_aarti.withColumn("Signal",
      when((df_aarti['rsi_14'] > 70) , lit("Overbought (Sell)")) 
     .when((df_aarti['rsi_14'] < 30) , lit("Oversold (Buy)"))
     .otherwise(lit("Neutral (hold)")))

In [0]:
# Strategy 3 - Using macd, macdsignal and macdhist
from pyspark.sql.functions import *
df3_aarti = df_aarti.withColumn("Buy_Signal", when((col("macd") > col("macdsignal")) & (col("macdhist") <= col("macdsignal")), "Buy").otherwise("Hold")) \
                 .withColumn("Sell_Signal", when((col("macd") < col("macdsignal")) & (col("macdhist") >= col("macdsignal")), "Sell").otherwise("Hold")) 

In [0]:
# Sending the data on kafka
for row in df1_aarti.collect():
    dict_stock = row.asDict()
    producer.send('demo_testing1', value=dict_stock)
    sleep(5)

In [0]:
# Sending the data on kafka
for row in df2_aarti.collect():
    dict_stock = row.asDict()
    producer.send('demo_testing1', value=dict_stock)
    sleep(5)

In [0]:
# Sending the data on kafka
for row in df3_aarti.collect():
    dict_stock = row.asDict()
    producer.send('demo_testing2', value=dict_stock)
    sleep(5)